In [7]:
import nltk
import numpy as np
import re
import string
import tensorflow as tf
from nltk.corpus import twitter_samples, stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout

In [3]:
# Download required NLTK resources
#nltk.download('twitter_samples')
#nltk.download('stopwords') and , or with because
#nltk.download('punkt') 
#nltk.download('wordnet')

In [8]:
# Load dataset
positive_tweets = twitter_samples.strings('positive_tweets.json')
negative_tweets = twitter_samples.strings('negative_tweets.json')
tweets = positive_tweets + negative_tweets # "" "" , "            "
labels = [1]*len(positive_tweets) + [0]*len(negative_tweets)

In [9]:
# Text cleaning function
def clean_text(text):
    text = text.lower()
    text = re.sub(r"http\S+|www\S+|https\S+", '', text)  # remove URLs
    text = re.sub(r"@\w+|#", '', text)  # remove mentions and hashtags
    text = re.sub(r"[^\w\s]", '', text)  # remove punctuation
    text = re.sub(r"\d+", '', text)  # remove digits
    text = text.strip() # []
    return text

In [10]:
# Preprocessing
stop_words = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()

In [11]:
def preprocess(text):
    text = clean_text(text)
    tokens = nltk.word_tokenize(text)
    tokens = [lemmatizer.lemmatize(w) for w in tokens if w not in stop_words and len(w) > 2]
    return " ".join(tokens)

In [12]:
processed_tweets = [preprocess(tweet) for tweet in tweets]


In [13]:
# Tokenization
tokenizer = Tokenizer(num_words=10000, oov_token='<OOV>')
tokenizer.fit_on_texts(processed_tweets)
sequences = tokenizer.texts_to_sequences(processed_tweets)
padded_sequences = pad_sequences(sequences, maxlen=50, padding='post', truncating='post')

In [14]:
# Train/test split
X_train, X_test, y_train, y_test = train_test_split(padded_sequences, labels, test_size=0.2, random_state=42)

In [20]:
from tensorflow.keras.layers import Bidirectional

# LSTM Model
model = Sequential([
    Embedding(input_dim=10000, output_dim=128, input_length=50),
    Bidirectional(LSTM(64, return_sequences=False)),
    Dropout(0.5),
    Dense(64, activation='relu'),
    Dropout(0.5),
    Dense(1, activation='sigmoid')
])

In [21]:
from tensorflow.keras.optimizers import Adam
model.compile(
    loss='binary_crossentropy',
    optimizer=Adam(learning_rate=0.0005),  # 🔧 slower learning
    metrics=['accuracy']
)

model.summary()


Model: "sequential_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ embedding_1 (Embedding)              │ ?                           │     0 (unbuilt) │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ bidirectional (Bidirectional)        │ ?                           │     0 (unbuilt) │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_2 (Dropout)                  │ ?                           │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_2 (Dense)                      │ ?                           │     0 (unbuilt) │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_3 (Dropout)                  │ ?                           │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_3 (Dense)                      │ ?                           │     0 (unbuilt) │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 0 (0.00 B)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 0 (0.00 B)

In [22]:
from tensorflow.keras.callbacks import EarlyStopping

early_stop = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)

history = model.fit(
    np.array(X_train), np.array(y_train),
    epochs=20,
    batch_size=32,
    validation_split=0.1,
    callbacks=[early_stop]
)


Epoch 1/20
225/225 ━━━━━━━━━━━━━━━━━━━━ 9s 21ms/step - accuracy: 0.5347 - loss: 0.6821 - val_accuracy: 0.7425 - val_loss: 0.4950
Epoch 2/20
225/225 ━━━━━━━━━━━━━━━━━━━━ 4s 19ms/step - accuracy: 0.8012 - loss: 0.4275 - val_accuracy: 0.7812 - val_loss: 0.4486
Epoch 3/20
225/225 ━━━━━━━━━━━━━━━━━━━━ 4s 19ms/step - accuracy: 0.8964 - loss: 0.2804 - val_accuracy: 0.7738 - val_loss: 0.4933
Epoch 4/20
225/225 ━━━━━━━━━━━━━━━━━━━━ 4s 19ms/step - accuracy: 0.9268 - loss: 0.1946 - val_accuracy: 0.7688 - val_loss: 0.5735
Epoch 5/20
225/225 ━━━━━━━━━━━━━━━━━━━━ 4s 18ms/step - accuracy: 0.9415 - loss: 0.1656 - val_accuracy: 0.7462 - val_loss: 0.6487


In [23]:
# Evaluation
loss, accuracy = model.evaluate(np.array(X_test), np.array(y_test))
print(f"Test Accuracy: {accuracy * 100:.2f}%")


63/63 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - accuracy: 0.7384 - loss: 0.4997
Test Accuracy: 75.90%


In [24]:
# Save the model
model.save("twitter_lstm_sentiment_model.h5")
print("Model saved successfully!")

Model saved successfully!


In [25]:
import pickle

# Save tokenizer
with open("tokenizer.pkl", "wb") as f:
    pickle.dump(tokenizer, f)

print("Tokenizer saved!")

Tokenizer saved!
